In [68]:
import pandas as pd
from io import StringIO
import requests
import spacy
import re
import difflib
import string
import spacy
import hunspell

Level                    Title  \
0    A1            Meine Familie   
1    A1   Maria und ihre Familie   
2    A1              Ich bin Tom   
3    A1              Freundinnen   
4    A1  Einkaufen im Supermarkt   

                                                Text  \
0  Zu meiner Familie gehören vier Personen. Die M...   
1  Mein Name ist Maria. Ich bin 30 Jahre alt. Zu ...   
2  Hallo! Ich bin Tom Maier. Ich bin 13 Jahre alt...   
3  Ricarda ist 21 Jahre alt und wohnt in Lübeck. ...   
4  Frau Meier geht heute in den Supermarkt. Ihr M...   

                                       Source cleanedSource     Type  
0         https://german.net/reading/familie/    german.net  Reading  
1  https://german.net/reading/marias-familie/    german.net  Reading  
2             https://german.net/reading/tom/    german.net  Reading  
3     https://german.net/reading/freundinnen/    german.net  Reading  
4       https://german.net/reading/einkaufen/    german.net  Reading

In [ ]:
def load_df_from_GoogleDocs():
    url = "https://docs.google.com/spreadsheets/d/e/2PACX-1vTSLyp3Ev2bxe8pnHStFtbdwg-EhvbMEhEUzRsaFjC0sKVQ-OzyD8LbAjM9iYoG2LSmSTAGGFfed4I9/pub?gid=0&single=true&output=csv"

    df=pd.read_csv(StringIO(requests.get(url).content.decode('utf-8')))
    display(df.head())
    return df

In [ ]:
# Initialize the spacy
spacyNLP = spacy.load('de')

# Initialize the Spellchecker
spellchecker = hunspell.HunSpell('/usr/share/hunspell/de_DE.dic',
                                 '/usr/share/hunspell/de_DE.aff')

correct = [",", "!", "?" , "\"", ":", "/", "*", "(", ")", "%", "-", ";"
           "Valerie", "Lena", "Lana", "Micki", "Maier", "Ricarda", "Maike", "Struppi", "Mayer", "Leonie", "Valerie", "Müritzsee",
          'Disko', 'Nikolaustag', 'Jana', 'blitzeblank', 'Urenkelkinder',"Ricardas", "Königstraße", "1234/567890", "Mimi", "Logistiker",
           "Stubbe", "Hohensalzburg", "Einkaufsbummel", "Röbel", "zusammenzuziehen", "Drogerieartikel", "Nadja", "Urenkelkind",
           "Na", "Ok", "heruntergesetzt", "T-Shirt", "Hey", "zuhause", "Aha", "Hostel", "Julian", "Rafting", "Paragliding",
           "Orang-Utans", "Pinguingehege", "Fütterungszeit", "Juliana", "Julianas", "Klara", "WG", "Goethehaus", "Leibgericht",
           "Marco", "Goethestraße", "Schillerstraße", "Michels", "Veronika", "Caroline", "Klassenbester", "Basketballer", "Granada",
           "Model", "Ca", "Ayurveda-Kuren", "Thalasso-Therapien", "Medical-Wellness-Urlaub", "Wellness-Urlaub", "1970er", "Burger",
           "Fastfood", "Tütensuppe", "Äh", "Tja", "Wow", "Ups", "Date", "Online-Dating", "Events", "Wroclaw",
           "Johann-August-Zeune-Schule", "euphorisieren", "euphorisierte", "schaften", "schaffen", "Shopping", "TOPCARD",
           "Ruhrtal-Radweg", "AStA", "Streetart-Gruppen",  "Shuttlebusse", "Alsdorf", "Helen", "CO2-Emissionen", "vietnamesische",
           "Halle/Saale", "Lynn", "Linda", "Phuong", "Pauline", "Brexit-Votum"]

for word in correct:
    spellchecker.add(word)

def isUmlautError(string, corrected):
    '''returns true if the only spelling error in a word consits of an Umlaut
    (important due to encoding error ins some datasets)'''
    matches = difflib.SequenceMatcher(None, corrected, string).get_matching_blocks()
    rest = list(corrected)
    for match in reversed(matches):
        rest[match.a:match.a + match.size] = []
    return set(rest)<set('äöüÄÖÜ') and len(set(rest)) > 0

def isCapitalisationError(string, corrected):
    '''returns true if the only detected spelling error is a cpitilisation error'''
    return (string[1:] == corrected[1:] and string[0].lower() == corrected[0].lower())


def spellcheck(text):
    '''spellcheck a text and return, beside the corrected version, some measures for spelling errors'''
    total=0
    numberSpellingErrorsWithCorrection=0
    numberSpellingErrorsWithoutCorrection=0
    numberUmlautSpellingErrors=0
    numberCapitalisationErrors=0
    
    correctedText = text
    for word in reversed(list(spacyNLP(text))):
        total+=1
        if not spellchecker.spell(word.text) and not word.text == " ": # and word not in exclude:
            try:
                suggestions = spellchecker.suggest(word.text)
                autocorrected = suggestions[0]
                index = word.idx
                length = len(word.text)
                print(str(word.text + " --> " + autocorrected))
                correctedText = correctedText[:index] + autocorrected + correctedText[index + length:]
                if isUmlautError(word.text, autocorrected):
                    print("UE")
                    numberUmlautSpellingErrors += 1
                elif isCapitalisationError(word.text, autocorrected):
                    print("CE")
                    numberCapitalisationErrors+=1
                numberSpellingErrorsWithCorrection+=1
            except IndexError:
                numberSpellingErrorsWithoutCorrection+=1
                print(str(word.text + " --> "))
    
    ratioSpellingErrorsWithCorrection = numberSpellingErrorsWithCorrection/total
    ratioSpellingErrorsWithoutCorrection = numberSpellingErrorsWithoutCorrection/total
    ratioSpellingErrors = (numberSpellingErrorsWithoutCorrection + numberSpellingErrorsWithCorrection)/total
    ratioUmlautSpellingErrors=numberUmlautSpellingErrors/total
    ratioCapitalisationErrors=numberCapitalisationErrors/total
    ratioRealSpellingErrors=(numberSpellingErrorsWithoutCorrection + numberSpellingErrorsWithCorrection - numberUmlautSpellingErrors - numberCapitalisationErrors) / total 
            
    return correctedText, ratioRealSpellingErrors, ratioSpellingErrors, ratioSpellingErrorsWithCorrection, ratioSpellingErrorsWithoutCorrection,ratioUmlautSpellingErrors, ratioCapitalisationErrors

def clean(text):
    '''Clean the text from non sentence sequences like headers in letters'''
    text, ratioRealSpellingErrors, ratioSpellingErrors, ratioSpellingErrorsWithCorrection, ratioSpellingErrorsWithoutCorrection,ratioUmlautSpellingErrors, ratioCapitalisationErrors = spellcheck(text)
    
    text = re.sub("Stadt X\,?\.?\s?(den )?\d+((\,)|(\.)|(\-))\d+((\,)|(\.)|(\. )|(\-))\d+ ", "", text)
    text = re.sub("^.{10,250}Sehr gee?h?e?e?rte?( Damen )?((und)|(oder))? He?er?ren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,100}Sehr Geherte mein Damen und Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,100}Liebe Dana", "Liebe Dana", text)
    text = re.sub("^.{10,100}Lieber? Silke", "Liebe Silke", text)
    text = re.sub("^.{10,100}Liebe Maria", "Liebe Maria", text)
    text = re.sub("^.{10,100}Liebe Katharina", "Liebe Katharina", text)
    text = re.sub("(\S+)\.(\S+)", r"\1. \2", text)
    text = re.sub("www. ", r"www.", text)
    text = re.sub("^.{10,100}Lieber Michael", "Lieber Michael", text)
    text = re.sub("^.{10,100}Lieber? Ingo", "Lieber Ingo", text)
    text = re.sub("^.{10,100}Lieber Julia", "Lieber Julia", text)
    text = re.sub("^.{10,100}Lieber Eva", "Lieber Eva", text)
    text = re.sub("^.{10,100}Hallo Eva", "Hallo Eva", text)
    text = re.sub("^.{10,100}Liebe Julia", "Liebe Julia", text)
    text = re.sub("^.{10,100}Lieber? Diana", "Liebe Diana", text)
    text = re.sub("^.{10,100}Hallo Julia", "Hallo Julia", text)
    text = re.sub("^.{10,100}Lieber? Jens", "Lieber Jens", text)
    text = re.sub("^.{10,200}Sehr geerhte Damen und Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Sehr Geehrte Damen und Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Sehr geehrte Damen und Herrn", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}See?hr gerrhte Herren und Damen", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Sehr geehte Damen und Herr", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Seehr geehrte Damen und Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Seher geherte Damen und Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Sehr geherte Herrn", "Sehr geehrte Herren", text)
    text = re.sub("^.{10,200}Sehr geehrte Fir", "Sehr geehrte Fir", text)
    text = re.sub("^.{10,200}Sehr geehrte Damen u. Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Sehr geehrte Damen u Herren", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^.{10,200}Seehr Geehrte Damen und He", "Sehr geehrte Damen und He", text)
    text = re.sub("^.{10,200}Sehr geehrte Au-", "Sehr geehrte Au-", text)
    text = re.sub("^.{10,200}SEHR GEEHRTE DAMEN UND HERREN", "Sehr geehrte Damen und Herren", text)
    text = re.sub("^STADT X 26.04. 2012 ", "", text)
    text = re.sub("^Stadt X, 22/02/2012 ", "", text)
    text = re.sub("^22.02. 2012 ", "", text)
    text = re.sub("^24.02. 12 ", "", text)
    text = re.sub("^Bahnhofsstraße 12 12345 ", "", text)
    text = re.sub("^Stadt X. 28.02. 2012. ", "", text)
    text = re.sub("^Stadt X 5. /3/2012 ", "", text)
    text = re.sub("^STADT X 04 17 ", "", text)
    text = re.sub("^04.17. 2012 ", "", text)
    text = re.sub("^Stadt X, 27.02. 2012. ", "", text)
    text = re.sub("^Stadt X 26.04. 12. ", "", text)
    text = re.sub("^16.03. 2012 ", "", text)
    text = re.sub("^Stadt X, 04 01 2012 ", "", text)
    text = re.sub("^Stadt X 05:01:2012 ", "", text)
    text = re.sub("^20. 01-2012 ", "", text)
    text = re.sub("^An die 19.01.0. 12 Wohnungsamt ", "", text)
    text = re.sub("^19.01. 12 ", "", text)
    text = re.sub("^Katharina Winkelmann Zentralplatz 12 12345 Stadt X Wohnungsamt. ", "", text)
    text = re.sub("^12.02. 12 ", "", text)
    text = re.sub("^Katharina Winkelmann Müllerdgasse 12 12345 Computer-Spezialist Ofenwaldstraße 5,m 53119 Bonn Bewerbung für Vertriebspraktikum. ", "", text)
    text = re.sub("^Julia Müller Bahnhof stur. 12 12345 Stadt X Vertrieb Praktikant w. /m Bahnhofstar. 5, 53119 Bonn ", "", text)
    text = re.sub("^Eva Winkelmann Müllerdgasse 12 12345 Stadt X. Computer-Spezialist Ofenwaldstraße 5, 53119 Bonn Praktikum als Kauffrau Beruf und Informatik, ", "", text)
    text = re.sub("^Computer-Spezialist Ofenwaldstraße 5 53119 Bonn Bewerbung als Vertriebspraktikantin ", "", text)
    text = re.sub("^Friedrich Winkelmann 16/0111/2011 Winkels weg 12 1234 Stadt X, Schweiz GLOBALISIER BAHNHOFSTR. 101 65185 WIESBADEN 0611/9988776 Objekt: Weitere Informationen / Internationale Au-Paar ", "", text)
    text = re.sub("^Maria Julia Meier Müller Bahnhofsstraße 1 12345 Stadt X E-Mail: maria.meier@internet.de Au-pair-Agentur Schultz & Partner Regenstr. 101 90451 Nürnberg Tel.: 0911/5544223 Fax: 0911/5544229 E-Mail: au-pair-schultz@web.de Stadt X, 29.07.2011 Beschweren an die Au-pair-Agentur Schultz ", "", text)
    text = re.sub("^Direktor SEXY Wohnungsamt Zentralplatz 123 Stadt X Per. Tobias Schmidt Akademie Klassenhof Bahnhofsstraße 123 Stadt Y 12345 Brauchen eine Wohnung ", "", text)
    text = re.sub("^Bahnhofsstoß 12 12345, Stadt X. Wohnungsamt. Winkels. - 321. Stadt X 10. März 12 ", "", text)
    text = re.sub("^Stadt Y darum hau Stadt Y, Fluss Eva Maria Stadt Z Neue Wohnung ", "", text)
    text = re.sub("^Tobias Meier Bahnhofsstar. 123 Winkels weg 321 Stadt X Stadt Y. 10.3. 12 ", "", text)
    text = re.sub("^12.3. 12", "" , text)
    text = re.sub("^Stefan Meier Zentralplatz 12 12-345 Stadt X Computer Spezialist Ofenwaldstraße 5 53119, Bonn Stadt X 7 Juli 2010 Bewerbung um eine Praktikum stelle ", "", text)
    text = re.sub("^Eva Winkelmann Zentralplatz 12/21 12-321 Stadt X Computer-Spezialist Ofenwaldstraße 5 53119 Bonn Bewerbung um ein Praktikum ", "", text)
    text = re.sub("^Maria Müller 11-222 Stadt Y Müllerdgasse 12/21 Polen Computer-Spezialist Ofenwaldstraße 5 53119 Bonn Bewerbung um ein Praktikum ", "", text)
    text = re.sub("^Michael Meier Müllerdgasse 12 12345 Stadt X Deutschland Globalisier Aufstreichen. 101, Datum 18.09. 2011 Information über Internationale Au-paar. ", "", text)
    text = re.sub("^Beschwerdebrief Maria Meier Stadt X Stadt X, am 7. Juli 2011. An die Au-paar-Agentur Schutz - Partner Regenstar. 101 90451 Nürnberg Betreff: Betreuung durch die Agentur. ", "", text)
    text = re.sub("^Au-paar-Agentur Schulz - Partner Regenstraße 101 90451 Nürnberg Maria Meier Bahnhofsstraße 123 12345 Stadt X Beschwerde ", "", text)
    text = re.sub("^Au-paar-Agentur Schulz - Partner Regenstar. 101 90451 Nürnberg Stadt X den, 01.08. 2011. Beschwerde. ", "", text)
    text = re.sub("^Bahnhofsstraße 1, 4321 Stadt X Deutschland. Au-paar-Agentur Schulz - Partner Regenstraße 101 90451 Regensburg 24. September 2011 ", "", text)
    text = re.sub("^Katharina Meier Müllerdgasse 12 12345 Stadt X Ukraine Teil: (0038) 0123456789 Globalisier Bahnhofstar. 101 65185 Wiesbaden 0611/9988776 ", "", text)
    text = re.sub("^1\) ", "", text)
    text = re.sub("1\. ", "", text)
    text = re.sub("\"", "", text)
    text = re.sub("  ", " ", text)
    
    return text, ratioRealSpellingErrors, ratioSpellingErrors, ratioSpellingErrorsWithCorrection, ratioSpellingErrorsWithoutCorrection,ratioUmlautSpellingErrors, ratioCapitalisationErrors

In [71]:
df.head()

Level                    Title  \
0    A1            Meine Familie   
1    A1   Maria und ihre Familie   
2    A1              Ich bin Tom   
3    A1              Freundinnen   
4    A1  Einkaufen im Supermarkt   

                                                Text  \
0  Zu meiner Familie gehören vier Personen. Die M...   
1  Mein Name ist Maria. Ich bin 30 Jahre alt. Zu ...   
2  Hallo! Ich bin Tom Maier. Ich bin 13 Jahre alt...   
3  Ricarda ist 21 Jahre alt und wohnt in Lübeck. ...   
4  Frau Meier geht heute in den Supermarkt. Ihr M...   

                                       Source cleanedSource     Type  
0         https://german.net/reading/familie/    german.net  Reading  
1  https://german.net/reading/marias-familie/    german.net  Reading  
2             https://german.net/reading/tom/    german.net  Reading  
3     https://german.net/reading/freundinnen/    german.net  Reading  
4       https://german.net/reading/einkaufen/    german.net  Reading

In [72]:
def setupRFTagger():
    '''The RFTagger module is downloaded and setup. This works only on Linux computers'''
    import urllib
    url = "http://www.cis.uni-muenchen.de/~schmid/tools/RFTagger/data/RFTagger.tar.gz"
    filename = "RFTagger.tar.gz"
    urllib.request.urlretrieve(url, filename)
    import tarfile
    tar = tarfile.open(filename)
    tar.extractall()
    tar.close()
    from subprocess import run
    run(["make"], cwd="RFTagger/src")
    
def setupParser():
    '''The Stanford Parser is set up to run in python'''
    #!pip install stanfordcorenlp
    #!apt install openjdk-11-jre
    import urllib
    import zipfile
    import shutil
    
    #download Stanford Parser
    url = "http://nlp.stanford.edu/software/stanford-corenlp-full-2018-02-27.zip"
    filename = "stanford-corenlp-full-2018-02-27.zip"
    urllib.request.urlretrieve(url, filename)
    
    zip_obj = zipfile.ZipFile(filename)
    zip_obj.extractall()
    zip_obj.close()

    url = "http://nlp.stanford.edu/software/stanford-german-corenlp-2018-02-27-models.jar"
    filename = "stanford-german-corenlp-2018-02-27-models.jar"
    urllib.request.urlretrieve(url, filename)

    shutil.move("./stanford-german-corenlp-2018-02-27-models.jar", "./stanford-corenlp-full-2018-02-27/stanford-german-corenlp-2018-02-27-models.jar")

In [73]:
from subprocess import check_output
from tqdm import tqdm
from stanfordcorenlp import StanfordCoreNLP
import re
import sys

    
def sentenceParsing(sentence, nlp):
    '''Parse a sentence using the stanford parser'''
    print(sentence.text)
    try:
        tree = re.sub(" +", " ", nlp.parse(sentence.text).replace("\n", ""))
        return tree
    except ValueError:
        return ""
        
    return output

def textTagging(sentenceList):
    '''Tag a sentence with the RFTagger'''
    tempFile = open("RFTagger/temp.txt", "w")
    tempFile.write("\n\n".join(["\n".join([word.text for word in sentence]) for sentence in sentenceList]))
    tempFile.close()
    text_tagged = check_output(["src/rft-annotate", "lib/german.par", "temp.txt"], cwd="RFTagger").decode("utf-8").split("\n\n")
    
    text_tagged_saparated = []
    for sentence_tagged in text_tagged:    
        sentence_tagged_saparated= []
        for entry in sentence_tagged.split('\n'):
            temp = entry.split("\t")
            if len(temp) == 2:
                sentence_tagged_saparated.append([temp[0]] + temp[1].split("."))
            elif len(temp) == 1 and temp[0] == '':
                continue
                
        text_tagged_saparated.append(sentence_tagged_saparated)
                
    return text_tagged_saparated[:-1]

def preprocessing(df):
    '''complete preprocessing pipeline for the data set, including the creation of a sentence data set'''
    df["newLevel"] = [element[0] for element in df["Level"]]
    spellcheckerResults = []
    for text in tqdm(df["Text"]):
        spellcheckerResults.append(clean(text))
    
    df["cleanedText"] = [spellcheckerResult[0] for spellcheckerResult in spellcheckerResults]
    df["SE_ratioRealSpellingErrors"]= [spellcheckerResult[1] for spellcheckerResult in spellcheckerResults]
    df["SE_ratioSpellingErrors"]= [spellcheckerResult[2] for spellcheckerResult in spellcheckerResults]
    df["SE_ratioSpellingErrorsWithCorrection"]= [spellcheckerResult[3] for spellcheckerResult in spellcheckerResults]
    df["SE_ratioSpellingErrorsWithoutCorrection"]= [spellcheckerResult[4] for spellcheckerResult in spellcheckerResults]
    df["SE_ratioUmlautSpellingErrors"]= [spellcheckerResult[5] for spellcheckerResult in spellcheckerResults]
    df["SE_ratioCapitalisationErrors"]= [spellcheckerResult[5] for spellcheckerResult in spellcheckerResults]
    
    del spellcheckerResults
    
    taggedTexts = []
    taggedSentences = []
    
    pasedTexts = []
    parsedSentences = []
    
    sentences = []
    sentenceLevels = []
    
    
    nlp = StanfordCoreNLP(r'./stanford-corenlp-full-2018-02-27', lang='de', memory='2g')
    
    for index, row in tqdm(df.iterrows()):
        doc = spacyNLP(row["cleanedText"])
        newParsedText = []
        
        newTaggedSentences = textTagging(list(doc.sents))
        
        for sentence in list(doc.sents):
            newParsedSentence = sentenceParsing(sentence, nlp)
            newParsedText.append(newParsedSentence)
            parsedSentences.append(newParsedSentence)

            sentences.append(sentence.text)
            sentenceLevels.append(row["newLevel"])

        taggedTexts.append(newTaggedSentences)
        taggedSentences += newTaggedSentences
        pasedTexts.append(newParsedText)
    
    nlp.close()  # Do not forget to close! The backend server will consume a lot memory.
    
    df["RFTagger"] = taggedTexts
    df["parsedText"] = pasedTexts
   
    sentence_df = pd.DataFrame()
    sentence_df["Text"] = sentences
    sentence_df["newLevel"] = sentenceLevels
    sentence_df["taggedSentences"] = taggedSentences
    sentence_df["parsedSentences"] = parsedSentences
    
    return df, sentence_df

In [74]:
df = load_df_from_GoogleDocs()
df, sentence_df = preprocessing(df)




  0%|          | 0/2563 [00:00<?, ?it/s]


  0%|          | 2/2563 [00:00<02:13, 19.21it/s]

0
0
0
0





  0%|          | 5/2563 [00:00<02:15, 18.85it/s]


  0%|          | 8/2563 [00:00<01:59, 21.38it/s]

0
0
0
0
0





  0%|          | 10/2563 [00:00<02:03, 20.66it/s]

...

Normalerweise erinnere ich mich die Wörter, die eine spezifische Bedeutung für mich haben, oder Wörter, die anders klingt dB Die Umgebung.
In der Zukunft werde ich meine Langzeitgedächtnis verbessern.
Wenn meine Langzeitgedächtnis besser wäre, wurde ich ein weitere Spektrum der Vokabeln haben.
Es wurde leichter für mich sein, Wörter zu erinnern.
Der Einfluss der Stars auf die Jugend iss zu groß geworden Heutzutage können die Stars die Jugend viel beeinflussen.
Ich meine, dass die Jugend noch nicht richtig und falsch wissen.
Ich finde, dass die Stars eine falsche Impression von Leben geben.
Leider ist es nicht möglich für jeden, reich und berühmt zu sein.
Es gibt positive Wirkungen wegen des Einflusses, aber die meisten sind negative.
Viele Menschen möchten aus ihre Helden sehen z. B. Viktoria Beckmann.
Wenn Viktoria Beckmann einen neuen Haarschnitt hätte, würden alle ihre Fans einen ähnlichen Haarschnitt haben wollen.
Manchmal werden Leute eine Schönheitsoperation haben, um die Charakt




2562it [2:06:57,  2.97s/it]

ich glaube, dass die Jugendliche sehr empfindungslose sind und sie ihre Intentionen nicht kontrollieren.
Daher müssen die Stars denken, bevor sie bestimmte Dinge machen.
Studiengebühren diskriminieren ärmere Studenten.
Stimmen Sie dieser Aussage zu?
Heutzutage ist es schwieriger für Studenten, Studien ohne finanzielle Unterstützung zu beenden.
leider müssen Studenten Gebühren bezahlen und diese Gebühren sind sehr teuer.
meiner Meinung nach wird ärmere Studenten diskriminiert, weil sie vielleicht keine Möglichkeit haben, um diese Gebühren zu bezahlen.
Wenn man ein Student ist, ist es schwer genug wegen anderen Kosten zu leben.
Bücher, Unterkunft und Essen müssen bezahlt werden!
Warum muss man mehr bezahlen?
Ich glaube, dass die Gebühren viele Menschen ermutigen können, nicht an der Universität zu kommen, besonders wenn sie arm sind.
Viele Familie von Studenten muss nochmal einen Arbeitsplatz finden, weil sie ohne mehr Geld nicht existieren konnten.
Wenn die Regierung mehr Staatshilfe gä




2563it [2:06:59,  2.97s/it]




ich bin fest davon überzeugt, dass die Diskriminierung von ärmeren Studenten halten muss.


In [75]:
df.head()

Level                    Title  \
0    A1            Meine Familie   
1    A1   Maria und ihre Familie   
2    A1              Ich bin Tom   
3    A1              Freundinnen   
4    A1  Einkaufen im Supermarkt   

                                                Text  \
0  Zu meiner Familie gehören vier Personen. Die M...   
1  Mein Name ist Maria. Ich bin 30 Jahre alt. Zu ...   
2  Hallo! Ich bin Tom Maier. Ich bin 13 Jahre alt...   
3  Ricarda ist 21 Jahre alt und wohnt in Lübeck. ...   
4  Frau Meier geht heute in den Supermarkt. Ihr M...   

                                       Source cleanedSource     Type newLevel  \
0         https://german.net/reading/familie/    german.net  Reading        A   
1  https://german.net/reading/marias-familie/    german.net  Reading        A   
2             https://german.net/reading/tom/    german.net  Reading        A   
3     https://german.net/reading/freundinnen/    german.net  Reading        A   
4       https://german.net/reading/einkaufen/    german.net  Reading        A   

                                         cleanedText  \
0  Zu meiner Familie gehören vier Personen. Die M...   
1  Mein Name ist Maria. Ich bin 30 Jahre alt. Zu ...   
2  Hallo! Ich bin Tom Maier. Ich bin 13 Jahre alt...   
3  Ricarda ist 21 Jahre alt und wohnt in Lübeck. ...   
4  Frau Meier geht heute in den Supermarkt. Ihr M...   

   SE_ratioRealSpellingErrors  SE_ratioSpellingErrors  \
0                         0.0                     0.0   
1                         0.0                     0.0   
2                         0.0                     0.0   
3                         0.0                     0.0   
4                         0.0                     0.0   

   SE_ratioSpellingErrorsWithCorrection  \
0                                   0.0   
1                                   0.0   
2                                   0.0   
3                                   0.0   
4                                   0.0   

   SE_ratioSpellingErrorsWithoutCorrection  SE_ratioUmlautSpellingErrors  \
0                                      0.0                           0.0   
1                                      0.0                           0.0   
2                                      0.0                           0.0   
3                                      0.0                           0.0   
4                                      0.0                           0.0   

   SE_ratioCapitalisationErrors  \
0                           0.0   
1                           0.0   
2                           0.0   
3                           0.0   
4                           0.0   

                                            RFTagger  \
0  [[[Zu, APPR, Dat], [meiner, PRO, Poss, Attr, -...   
1  [[[Mein, PRO, Poss, Attr, -, Nom, Sg, Masc], [...   
2  [[[Hallo, ITJ], [!, SYM, Pun, Sent]], [[Ich, P...   
3  [[[Ricarda, N, Name, Nom, Sg, Fem], [ist, VFIN...   
4  [[[Frau, N, Reg, Nom, Sg, Fem], [Meier, N, Nam...   

                                          parsedText  
0  [(ROOT (S (PP (APPR Zu) (PPOSAT meiner) (NN Fa...  
1  [(ROOT (S (NP (PPOSAT Mein) (NN Name)) (VAFIN ...  
2  [(ROOT (NUR (ITJ Hallo) ($. !))), (ROOT (S (PP...  
3  [(ROOT (CS (S (NE Ricarda) (VAFIN ist) (AP (NP...  
4  [(ROOT (S (NP (NN Frau) (NE Meier)) (VVFIN geh...

In [76]:
sentence_df.head()

Text newLevel  \
0           Zu meiner Familie gehören vier Personen.        A   
1  Die Mutter bin ich und dann gehört natürlich m...        A   
2  Wir haben zwei Kinder, einen Sohn, der sechs J...        A   
3  Wir wohnen in einem kleinen Haus mit einem Gar...        A   
4       Dort können die Kinder ein bisschen spielen.        A   

                                     taggedSentences  \
0  [[Zu, APPR, Dat], [meiner, PRO, Poss, Attr, -,...   
1  [[Die, ART, Def, Nom, Sg, Fem], [Mutter, N, Re...   
2  [[Wir, PRO, Pers, Subst, 1, Nom, Pl, *], [habe...   
3  [[Wir, PRO, Pers, Subst, 1, Nom, Pl, *], [wohn...   
4  [[Dort, ADV], [können, VFIN, Mod, 3, Pl, Pres,...   

                                     parsedSentences  
0  (ROOT (S (PP (APPR Zu) (PPOSAT meiner) (NN Fam...  
1  (ROOT (CS (S (NP (ART Die) (NN Mutter)) (VAFIN...  
2  (ROOT (S (PPER Wir) (VAFIN haben) (CNP (NP (CA...  
3  (ROOT (S (PPER Wir) (VVFIN wohnen) (PP (APPR i...  
4  (ROOT (S (ADV Dort) (VMFIN können) (NP (ART di...

In [77]:
def save_df(path,df):
    df.to_csv(path,sep="|",index=False)
    
display(df.head(100))
filename = "datasets/01_Preprocessing_df.csv"
save_df(filename, df)

display(sentence_df.head(n=100))
filename = "datasets/01a_Sentence_df.csv"
save_df(filename, sentence_df)

Level                                  Title  \
0     A1                          Meine Familie   
1     A1                 Maria und ihre Familie   
2     A1                            Ich bin Tom   
3     A1                            Freundinnen   
4     A1                Einkaufen im Supermarkt   
5     A1                              Frühstück   
6     A1           Susanne schreibt einen Brief   
7     A1                          Der Skiurlaub   
8     A1                                Struppi   
9     A1                          In der Schule   
10    A1           Martin, Leonie und Christian   
11    A1                        Brief an Marion   
12    A2                        Einkaufen gehen   
13    A2                             Österreich   
14    A2                 Der Weg zum Supermarkt   
15    A1                                 Ferien   
16    A2                     Wir sind umgezogen   
17    A2                               Umtausch   
18    A2                          Der Müritzsee   
19    A2                 Meine Geburtstagsfeier   
20    B1                              Der Umzug   
21    A2                     Im Einkaufszentrum   
22    A2                               Mein Tag   
23    A2                          Was will Tom?   
24    B1              Morgen kommt der Nikolaus   
25    B1                        Omas Geburtstag   
26    A2                    Meine erste Wohnung   
27    A2                            Meine Stadt   
28    B1                              Beim Arzt   
29    A2                        Kleidung kaufen   
..   ...                                    ...   
70    A1                     Ab in den Urlaub 3   
71    A1                      Essen und Trinken   
72    A2                  Familiengeschichten 1   
73    A2                  Familiengeschichten 2   
74    A2                  Familiengeschichten 3   
75    A2                  Familiengeschichten 4   
76    A2                  Familiengeschichten 5   
77    A2                  Familiengeschichten 6   
78    A2                              Unterwegs   
79    A2                   Freizeit und Hobby 1   
80    A2                   Freizeit und Hobby 2   
81    A2                   Freizeit und Hobby 3   
82    A2                          Leute treffen   
83    A2                         Kultur erleben   
84    A2                       Mit allen Sinnen   
85    A2                  Ideen und Erfindungen   
86    B1                              Zeitpunkt   
87    B1  Männer - Frauen - Paare - Studio [21]   
88    B1                 Fußball in Deutschland   
89    B1                       Das Ruhrgebiet 1   
90    B1                       Das Ruhrgebiet 2   
91    B1                       Das Ruhrgebiet 3   
92    B1                       Das Ruhrgebiet 4   
93    B1                      Schule und lernen   
94    B1                       Klima und Umwelt   
95    B1             Das ist mir aber peinlich!   
96    B1                           Generationen   
97    B1                              Migration   
98    B1                               Europa 1   
99    B1                               Europa 2   

                                                 Text  \
0   Zu meiner Familie gehören vier Personen. Die M...   
1   Mein Name ist Maria. Ich bin 30 Jahre alt. Zu ...   
2   Hallo! Ich bin Tom Maier. Ich bin 13 Jahre alt...   
3   Ricarda ist 21 Jahre alt und wohnt in Lübeck. ...   
4   Frau Meier geht heute in den Supermarkt. Ihr M...   
5   Es ist 7 Uhr am Morgen. Familie Müller sitzt a...   
6   Lieber Thomas! Jetzt bist du weit weg! Ich bin...   
7   Hartmut hat im Februar eine Reise gemacht: Er ...   
8   Jan hat einen kleinen Hund. Er heißt Struppi u...   
9   Heute ist der erste Schultag. Lena steht mit i...   
10  Martin Stubbe ist 15 Jahre alt. Er lebt mit se...   
11  Hallo Marion, ich bin es, dein Daniel. Ich hof...   
12  Heute ist Freitag. Wir haben heute Morgen in u...   
13  Im Sommer reisen viele Menschen gerne 

Text newLevel  \
0            Zu meiner Familie gehören vier Personen.        A   
1   Die Mutter bin ich und dann gehört natürlich m...        A   
2   Wir haben zwei Kinder, einen Sohn, der sechs J...        A   
3   Wir wohnen in einem kleinen Haus mit einem Gar...        A   
4        Dort können die Kinder ein bisschen spielen.        A   
5   Unser Sohn kommt bald in die Schule, unsere To...        A   
6           Meine Kinder sind am Nachmittag zu Hause.        A   
7                        So arbeite ich nur halbtags.        A   
8   Eigentlich gehören zu unserer Familie auch noc...        A   
9                           Sie wohnen nicht bei uns.        A   
10                    Sie haben ein Haus in der Nähe.        A   
11                 Die Kinder gehen sie oft besuchen.        A   
12                               Mein Name ist Maria.        A   
13                              Ich bin 30 Jahre alt.        A   
14  Zu meiner Familie gehören außer mir noch drei ...        A   
15                 Mein Mann Markus ist 31 Jahre alt.        A   
16                             Wir haben zwei Kinder.        A   
17            Unser Sohn Heinrich ist drei Jahre alt.        A   
18           Unsere Tochter Valerie ist ein Jahr alt.        A   
19         Wir haben auch einen Hund und zwei Katzen.        A   
20  Der Hund heißt Maya und die Katzen Lana und Mi...        A   
21                          Wir wohnen in einem Dorf.        A   
22         Die Stadt ist nicht weit von uns entfernt.        A   
23         Unser Haus ist klein und hat einen Garten.        A   
24                     Dort spielen die Kinder gerne.        A   
25  Heinrich geht in den Kindergarten, und Valerie...        A   
26  Meine Eltern leben im Ausland, aber die Eltern...        A   
27       Ich gehe sie mit den Kindern gerne besuchen.        A   
28            Oft passen sie auch auf die Kinder auf.        A   
29  Ich bin Journalistin und arbeite meistens von ...        A   
..                                                ...      ...   
70  Im Café neben dem Supermarkt gibt es sehr gute...        A   
71                                        Frau Meier:        A   
72  Gute Idee!. Frau Meier und Frau Schmidt gehen ...        A   
73                   Frau Meier: Ich brauche Tomaten.        A   
74                        Mein Mann will Salat essen.        A   
75                            Ich nehme zehn Tomaten.        A   
76                                      Frau Schmidt:        A   
77                                  Tomaten sind gut.        A   
78                            Ich kaufe fünf Tomaten.        A   
79                             Da ist auch Kopfsalat.        A   
80                 Frau Meier nimmt keinen Kopfsalat.        A   
81                        Sie nimmt aber zwei Gurken.        A   
82           Frau Meier kauft auch ein Kilo Zwiebeln.        A   
83                     Frau Schmidt will Brot kaufen.        A   
84              Frau Meier: Das Brot ist nicht schön.        A   
85                    Ich kaufe Brot in der Bäckerei.        A   
86                  Aber die Schokolade hier ist gut.        A   
87                            Sie kostet nur 50 Cent.        A   
88                  Ich nehme drei Tafeln Schokolade.        A   
89                                      Frau Schmidt:        A   
90                     Da ist noch ein Sonderangebot.        A   
91         Mineralwasser und Orangensaft sind billig.        A   
92                                        Frau Meier:        A   
93                     Orangensaft habe ich zu Hause.        A   
94      Aber ich brauche fünf Flaschen Mineralwasser.        A   
95  Frau Schmidt kauft nur drei Flaschen Mineralwa...        A   
96    Frau Meier und Frau Schmidt gehen an die Kasse.        A   
97                           Dann gehen sie ins Café.        A   
98                Frau Schmidt trinkt eine Tasse Tee.        A   
99                     